#### This program aims to recreate the plots and diagrams in Section 5.2 of Physics by Computer by Kinzel and Reents.

## 5.2 Fractal Aggregates

The deposition of material on the electrode does not lead to a compact object; instead a filligree-like cluster emerges, which can be described by a fractal dimension D. This process is called diffusion limited aggregation (DLA). 

Consider a random walk on a d-dimensional cubic lattice. We designate the lattice vectors by x and the vectors connecting a lattice site to its 2d nearest neighbors by $\Delta x_i,\ i=1,2,...,2d$. The motion of the random walker is defined by: randomly select one of the nearest neighbor sites $x+\Delta x_i$ and jump there during the next time step $\Delta t$. By following this process, we obtain the following balance equation

$$u(x,t+\Delta t) - u(x,t) = \frac{1}{2d} \sum_{i=1}^{2d}(u(x+\Delta x_i,t) - u(x,t))$$

where u(x,t) is the fraction that will be at the site x at time t.

We divide this equation by a suitable volume, to obtain a density, and by $\Delta t$. We also let all small quantities, all $\Delta x_i$ go to 0 in proportion to $\sqrt{\Delta t}$. This leads to the equation

$$\frac{\partial u}{\partial t} = \eta \nabla^2 u$$

for the probability density, with a diffusion constant $\eta$.

This equation can be solved with the initial condition $u(x,t_o) = \delta(x-x_o)$ and the boundary condition $u \to 0$ for $|x| \to \infty$ can be solved by a Fourier transformation. For $t \geq t_o$ one obtains

$$u(x,t) = [4\pi \eta(t-t_o)]^{-d/2} exp\Big(-\frac{|x-x_o|^2}{4\eta (t-t_o)}\Big)$$

From this we see that, the probability of finding the jumping particle at x at a later time t only depends on the distance $r = |x-x_o|$, not on the direction. The mean value is

$$\langle(x-x_o)^2\rangle = 2d \eta (t-t_o)$$

which means that the average size of the random path increases as $\sqrt{t-t_o}$. 

The model of Witten and Sander describes a diffusion limited growth process which proceeds according to the following rules.
1. Start with a minimal cluster.
2. Another particle starts diffusing freely at a great distance and at a randomly selected direction.
3. Does this until it hits nucleus at the origin and attaches to it.
4. The next particles starts far out again, and repeats this process.

When averaged over many iterations the cluster will grow in a radially symmetric way. Its fractal dimension can be determined as

$$M \approx R^D_{max}$$

where $R_{max}$ is the maximum radial size of the cluster and M is its mass. 

Assuming that all particles that get to within a certain capture radius $R_C$ are removed by absorption. We can replace $R_C$ by $R_{max}$ since they are proportional to each other. We will also assume that the time it takes a diffusing particle to move from one site to the next is much smaller than the time that characterizes the growth of the cluster. Using the boundary condition $u(R_{max})$,

$$\Delta u - \frac{1}{r^{d-1}}\frac{\partial}{\partial r} r^{d-1} \frac{\partial}{\partial r} u = 0$$

For d=2, we get

$$u(r) = u_o \Big(1-\big(\frac{R_{max}}{r}\big)^{d-2}\Big)$$

By integrating this over the surface, we obtain the results that the total particle current J is absorbed by the cluster is proportional to $R_{max}^{d-2}$. J is proportional to the increase in mass, which leads to the following equation

$$R_{max}^{d-2} \propto J = \frac{dM}{dt} = \frac{dM}{dR_{max}} \frac{dR_{max}}{dt} \propto R_{max}^{D-1}v$$

This means that the velocity v with which the cluster size increases is proportional to $R_{max}^{d-1-D}$. The exponent $d-1-D$ must not be positive (i.e. $d-1 \leq D$). The DLA cluster is embedded in a d-dimensional space, so we obtain the relation

$$d-1 \leq D \leq d$$
which has been confirmed for d=2,3,...,8 by numerical simulations.

The fractal dimension $D$ is given by

$$D = \frac{ln\ N}{ln\ R_{max}}$$

where $N$ is the number of particles in the aggregate, and $R_{max}$ is the aggreaget radius.

In [9]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animate
import matplotlib.cm as cm
from IPython.display import HTML

###  Place a particle on a random site at a distance $R_s > R_{max}$

In [2]:
def random_site(): 
    global R_s #radius of circle
    
    theta = np.random.random()*(2*np.pi) #random angle on unit circle
    x_val = R_s*np.cos(theta) #x value 
    y_val = R_s*np.sin(theta) #y value
    
    return x_val, y_val

### Random step to neighboring cells

In [4]:
def jump(x_val,y_val):
    step = np.random.randint(0,4)
    if step == 0: #to the right
        x_val += 1
    elif step == 1: #to the left
        x_val -= 1
    elif step == 2: #up
        y_val += 1
    else: #down
        y_val -= 1
    
    return x_val, y_val

### Positioned on a randomly selected site on a circle with radius $R-R_s$ around its current position

In [5]:
def circle(x_val,y_val): 
    
    global R_s #radius of circle
    
    R = np.sqrt(x_val**2 + y_val**2) #radius of new circle
    theta = np.random.random()*(2*np.pi) #random angle on new circle
    x_val += (R-R_s)*np.cos(theta) 
    y_val += (R-R_s)*np.sin(theta)
    
    return x_val,y_val

### Particle reaches a site near the aggregate, and is added to the aggregate

In [6]:
def aggregate(x_val,y_val):
    global R_max, N
    x, y = int(x_val//1), int(y_val//1) #x and y values must be integers
    
    empty_lattice[x+N,y+N] = 1
    
    R = np.sqrt(x**2 + y**2)
    R_max = max(R_max,R) #new radius of the aggregate

    if R_max > N-20: #arbitrary stopping condition; limits the size of the final aggregate
        stop = 1
    else: 
        stop = 0
    return stop

### Check the status of the particle

In [7]:
def checker(x_val,y_val):
    global N, R_k, R_d
    
    x, y = int(x_val//1), int(y_val//1) # x and y values must be integers
    R = np.sqrt(x**2 + y**2) #get radius of the current position of the particle from the center
    
    if R >= R_k: #particle exceeded the kill radius
        return 'k'
    elif R >= R_d: #particle exceeded Rd
        return 'c'
    elif (empty_lattice[x + 1 + N][y + N] + 
        empty_lattice[x - 1 + N][y + N] + 
        empty_lattice[x + N][y + 1 + N] + 
        empty_lattice[x + N][y - 1 + N] > 0): #particle reached a site adjacent to the aggregate
        return 'a'
    else: #nothing special so the particle just jumps to another adjacent site
        return 'j'

### Declare constants and initial conditions

In [10]:
R_max = 1 #actual size of the aggregate
R_s = R_max + 5
R_d = R_max + 10
R_k = 50*R_max #kill radius
counter = 1
D = 1

N = 100
empty_lattice = np.zeros((2*N,2*N)) #start with empty square lattice
empty_lattice[N, N] = 1 #put a particle at center of lattice
fig = plt.figure()
ax = fig.add_subplot(111)
ims = []
plt.close()

The next section of the code follows these steps:
1. Start with an empty square lattice and position a particle on the central lattice site.
2. Let the actual size of the aggregate be defined by the radius $R_{max}$. Place a particle on arandomly selected site at a distance $R_s > R_{max}$ from the origin and let it jump to a randomly selected adjacent site.
3. If the particle reaches a site adjacent to the aggregate, it is added and $R_{max}$ is increased if necessary. If the particle exceeds the distance $R_d > R_s > R_{max}$ from the origin - the actual distance is denoted by R - it is positioned on a randomly selected site on a circle around its current position with radius $(R - R_s)$. If the particle exceeds the distance $R_k > R_d > R_s > R_{max}$, it is annihilated.
4. Iterate steps 2 and 3 and calculate D.

In [14]:
stop = 0
x_val, y_val = random_site() #put particle at random radius Rs from center of lattice

while stop == 0:
    status = checker(x_val,y_val) #check the status of the particle
    
    if status == 'k': #particle exceeded kill radius and is annihilated
        x_val, y_val = random_site() #generate a new particle in a random radius from the center
        x_val, y_val = jump(x_val,y_val) #jump to an adjacent cell
        
    elif status == 'j': #particle jumps to an adjacent cell
        x_val, y_val = jump(x_val,y_val)
        
    elif status == 'c': #particle exceeded Rd and is position on the circle with radius R-Rs from its current position
        x_val, y_val = circle(x_val,y_val)

    elif status == 'a': #particle reaches a cell adjacent to the aggregate
        stop = aggregate(x_val,y_val) #particle aggregates
        #adjust new values depending on the new size of the aggregate
        R_k = 50*R_max
        R_s = R_max + 5
        R_d = R_max + 10
        counter += 1
        
        #calculated fractal dimension
        if R_max == 1:
            D = 1
        else:
            D = np.log(counter)/np.log(R_max)

        im = ax.matshow(empty_lattice , cmap=cm.gray_r, animated=True)
        ax.axis('off')
        t = ax.annotate("D = " + str(D),(1,0))
        ims.append([im, t])

        x_val, y_val = random_site() #generate a new particle
        x_val, y_val = jump(x_val,y_val) #jump to adjacent cell
    
    if counter > 1000: #arbitrary stopping condition
        stop = 1

### Animate the aggregate growth and watch how the fractal dimension increases

In [13]:
ani = animate.ArtistAnimation(fig, ims, interval=20, blit=True, repeat_delay=1000)
HTML(ani.to_jshtml(fps=20))